In [ ]:
# !jupyter nbextension enable --py widgetsnbextension

# Import Libraries and Modzy SDK

In [10]:
from modzy import ApiClient
from bs4 import BeautifulSoup
import requests
import IPython
from api_key import API_KEY

# Web Scraping CoinDesk RSS Feed

In [3]:
feel_url = "https://www.coindesk.com/arc/outboundfeeds/rss/?outputType=xml"
try:
    r = requests.get(feel_url)
    print(r.status_code)
except requests.exceptions.RequestException as e:
    print(e)  

200


In [6]:
soup = BeautifulSoup(r.content, features='xml')
articles = soup.findAll("item")
len(articles)

42

In [9]:
news_list = []

for a in articles:
    title = a.find('title').text
    link = a.find('link').text
    published = a.find('pubDate').text
    text = a.find('content:encoded').text
    article = {
        'title': title,
        'link': link,
        'published': published,
        'text': text
    }
    news_list.append(article)
    
news_list

[{'title': 'The Innovation at the Heart of the Global Crypto Transformation',
  'link': 'https://www.coindesk.com/podcasts/the-breakdown-with-nlw/the-innovation-at-the-heart-of-the-global-crypto-transformation',
  'published': 'Sun, 05 Dec 2021 14:00:00 +0000',
  'text': '<p><i>This episode is sponsored by </i><a href="https://nydig.com/nlw/?utm_source=coindesk&utm_medium=podcast&utm_campaign=nlw" target="_blank"><i>NYDIG</i></a><i>.</i></p><p><a href="https://rss.art19.com/episodes/cd302bd7-639b-4392-9467-26ccf3f531ff.mp3" target="_blank">Download this episode</a></p><p>This week’s Long Reads Sunday is a reading of Dan Jeffries’ “<a href="https://www.coindesk.com/business/2021/11/29/the-future-of-money-a-history/" target="_blank">The Future of Money: A History</a>.”</p><p><i>“The Breakdown” is written, produced by and features Nathaniel Whittemore aka NLW, with editing by Rob Mitchell, research by Scott Hill and additional production support by Eleanor Pahl. Adam B. Levine is our exec

# Web Scraping CoinDesk Webpage 

In [36]:
# web scraping article from CoinDesk webpage
# url = "https://www.coindesk.com/markets/2021/11/30/market-wrap-bitcoin-underperforms-as-ether-and-other-altcoins-rise/" 
# url = "https://www.coindesk.com/markets/2021/11/29/market-wrap-bitcoin-bears-retreat-as-traders-buy-on-dips/" 
url = "https://www.coindesk.com/tech/2021/11/30/ethereum-in-2022-what-is-money-in-the-metaverse/" 
try:
    r = requests.get(url)
    print(r.status_code)
except requests.exceptions.RequestException as e:
    print(e)   

200


In [21]:
soup = BeautifulSoup(r.content, features='html.parser')

title = soup.find('div', class_='at-headline').text
paragraphs = soup.findAll('div',class_='at-text')
article = ''.join([p.text for p in paragraphs])

print(f"title: \n{title}")
print()
print(f"article: \n{article}")

title: 
Ethereum in 2022: What Is Money in the Metaverse?

article: 
Ethereum is a smart-contract blockchain focused on building a secure, decentralized environment to host applications of all types. The past year, decentralized finance (DeFi) and non-fungible tokens (NFT) have taken the stage to show the world the possibilities that can arise from blockchain technology. However, scalability products that can increase performance in response to changes in processing demands are starting to unlock the vast potential Ethereum holds, and its co-creator, Vitalik Buterin, has his eyes set on decentralizing social media, gaming, governance and more.In its infancy, Ethereum has largely become host to marketplaces for trading and lending crypto assets (Uniswap and Aave) and buying or selling digital art (OpenSea). The introduction of second-layer platforms built on top of Ethereum, like Arbitrum and Optimism, and technological solutions like ZK rollups, will drag down transaction fees and open

# Initialize Modzy API Client

In [4]:
# create modzy client
client = ApiClient(base_url="https://app.modzy.com/api", api_key=API_KEY)

# Submit Text Summarization Job

In [22]:
sources = {}

# Add any number of inputs
sources["input_1"] = {
    "input.txt": article,
}

# submit the job
print("running text summarization job...")
job = client.jobs.submit_text("rs2qqwbjwb", "0.0.2", sources)
print(f"job: {job}")

result = client.results.block_until_complete(job, timeout=None)
print("running text summarization job...DONE")

running text summarization job...
job: Job(job_identifier='8f32d814-dfdc-479f-be67-5c18a36d1771',status='SUBMITTED')
running text summarization job...DONE


In [23]:
result = client.results.get(job.job_identifier)
result

Result({
  "accountIdentifier": "modzy-account",
  "averageModelLatency": 184.0,
  "completed": 1,
  "elapsedTime": 1745,
  "explained": false,
  "failed": 0,
  "finished": true,
  "initialQueueTime": 606,
  "inputSize": 445,
  "jobIdentifier": "8f32d814-dfdc-479f-be67-5c18a36d1771",
  "resultSummarizing": 206,
  "results": {
    "1": {
      "endTime": "2021-12-05T04:17:23.649+0000",
      "engine": "model-batch-rs2qqwbjwb-0-0-2-c8c7dd489-7fc77",
      "inputFetching": 151,
      "modelLatency": 184.0,
      "outputUploading": null,
      "queueTime": 606,
      "results.json": {
        "summary": "Ethereum is a smart-contract blockchain. The introduction of second-layer platforms will drag down transaction fees and open ethereum. scalability products that can increase performance in response to changes in processing demands are starting to unlock the potential ethereum holds. The past year, decentralized finance (DEFI) and non-fungible tokens have taken the stage. The native asset i

In [24]:
summary = result.get_first_outputs()['results.json']['summary']
summary

'Ethereum is a smart-contract blockchain. The introduction of second-layer platforms will drag down transaction fees and open ethereum. scalability products that can increase performance in response to changes in processing demands are starting to unlock the potential ethereum holds. The past year, decentralized finance (DEFI) and non-fungible tokens have taken the stage. The native asset is to the network what gas is to a car.'

In [28]:
# concatenare title and summary
summary_with_title = 'Title: ' + title + ' Summary: ' + summary
summary_with_title

'Title: Ethereum in 2022: What Is Money in the Metaverse? Summary: Ethereum is a smart-contract blockchain. The introduction of second-layer platforms will drag down transaction fees and open ethereum. scalability products that can increase performance in response to changes in processing demands are starting to unlock the potential ethereum holds. The past year, decentralized finance (DEFI) and non-fungible tokens have taken the stage. The native asset is to the network what gas is to a car.'

# Submit Text to Speech Job


In [29]:
sources = {}

# sample_text = 'Analysts view the rotation from Bitcoin to altcoins as an indicator of greater appetite for risk.'

#Add any number of inputs
sources["input_1"] = {
    "input.txt": summary_with_title,
}

# submit the job
print("running text-to-speech job...")
job = client.jobs.submit_text("uvdncymn6q", "0.0.3", sources)
print(f"job: {job}")


speech = client.results.block_until_complete(job, timeout=None)
print("running text-to-speech job...DONE")

running text-to-speech job...
job: Job(job_identifier='09d7f861-6c3e-4b9f-96ba-b6f8197432ce',status='SUBMITTED')
running text-to-speech job...DONE


In [30]:
result = client.results.get(job.job_identifier)
result

Result({
  "accountIdentifier": "modzy-account",
  "averageModelLatency": 174.0,
  "completed": 1,
  "elapsedTime": 220430,
  "explained": false,
  "failed": 0,
  "finished": true,
  "initialQueueTime": 538,
  "inputSize": 3267642,
  "jobIdentifier": "09d7f861-6c3e-4b9f-96ba-b6f8197432ce",
  "resultSummarizing": 928,
  "results": {
    "1": {
      "endTime": "2021-12-05T04:23:32.873+0000",
      "engine": "model-batch-uvdncymn6q-0-0-3-6f5d7b5fd9-8z6hx",
      "inputFetching": 168,
      "modelLatency": 174.0,
      "outputUploading": null,
      "queueTime": 538,
      "results.wav": "https://app.modzy.com/api/results/09d7f861-6c3e-4b9f-96ba-b6f8197432ce/1/results.wav",
      "startTime": "2021-12-05T04:19:54.102+0000",
      "status": "SUCCESSFUL",
      "updateTime": "2021-12-05T04:23:32.873+0000",
      "voting": {
        "down": 0,
        "up": 0
      }
    }
  },
  "startingResultSummarizing": "2021-12-05T04:23:33.072+00:00",
  "submittedAt": "2021-12-05T04:19:53.570+00:00",
 

In [31]:
# get result .wav file from modzy
wav_url = result.get_first_outputs()['results.wav']

headers = {
    'Accept': 'application/json', 
    'Authorization': f'ApiKey {API_KEY}'
}

wav =  requests.get(wav_url, headers=headers)
wav

<Response [200]>

# Play Audio Summary

In [32]:
# play audio
IPython.display.Audio(wav.content)

In [19]:
# save audio file            
with open('audio.wav', 'wb') as f:
     f.write(wav.content)

In [ ]:
# with requests.get(wav_url, headers=headers, auth=None, stream=True) as r:
#     with open('audio.wav', 'wb') as f:
#         for chunk in r.iter_content(chunk_size=8192):
#             f.write(chunk)

# IPython.display.display(IPython.display.Audio('audio.wav'))
# IPython.display.display(IPython.display.Audio(r.content))

# with open('market.txt', 'r', encoding='utf8') as file:
#     input_txt = file.read().replace('\n', '')
# print(input_txt)